# QRT ENS Challenge Data 2023 - Benchmark

Version 1 - Boosting, Feature engeneering & XGBoost 

## Librairies

In [15]:
import numpy as np
import pandas as pd
from scipy.stats import spearmanr
import xgboost as xgb
import matplotlib.pyplot as plt

from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import lightgbm as lgb
from joblib import dump

from lightgbm import LGBMRegressor
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import make_scorer

import warnings
warnings.filterwarnings('ignore')

## Chargement des données

- `X_train` et `X_test` ont  $35$ colonnes qui représentent les même variables explicatives mais sur des périodes de temps différentes. 

- `X_train` et `Y_train` partagent la même colonne `ID` - chaque ligne a un ID unique associé à un jour et à un pays. 

- La variable cible `TARGET` de `Y_train` correspond à la variation de prix journalière des futures sur l'électricité (maturité 24h).

- **On notera que certaines colonnes ont des valeurs manquantes**.


In [2]:
# After downloading the X_train/X_test/Y_train .csv files in your working directory:

X_train = pd.read_csv('../data/X_train.csv')
Y_train = pd.read_csv('../data/y_train.csv')
X_test = pd.read_csv('../data/X_test.csv')

In [3]:
X_train.head()

ID  DAY_ID COUNTRY  DE_CONSUMPTION  FR_CONSUMPTION  DE_FR_EXCHANGE  \
0  1054     206      FR        0.210099       -0.427458       -0.606523   
1  2049     501      FR       -0.022399       -1.003452       -0.022063   
2  1924     687      FR        1.395035        1.978665        1.021305   
3   297     720      DE       -0.983324       -0.849198       -0.839586   
4  1101     818      FR        0.143807       -0.617038       -0.924990   

   FR_DE_EXCHANGE  DE_NET_EXPORT  FR_NET_EXPORT  DE_NET_IMPORT  ...  \
0        0.606523            NaN       0.692860            NaN  ...   
1        0.022063      -0.573520      -1.130838       0.573520  ...   
2       -1.021305      -0.622021      -1.682587       0.622021  ...   
3        0.839586      -0.270870       0.563230       0.270870  ...   
4        0.924990            NaN       0.990324            NaN  ...   

   FR_RESIDUAL_LOAD   DE_RAIN   FR_RAIN   DE_WIND   FR_WIND   DE_TEMP  \
0         -0.444661 -0.172680 -0.556356 -0.790823 -0.283160 -1.069070   
1         -1.183194 -1.240300 -0.770457  1.522331  0.828412  0.437419   
2          1.947273 -0.480700 -0.313338  0.431134  0.487608  0.684884   
3         -0.976974 -1.114838 -0.507570 -0.499409 -0.236249  0.350938   
4         -0.526267 -0.541465 -0.424550 -1.088158 -1.011560  0.614338   

    FR_TEMP   GAS_RET  COAL_RET  CARBON_RET  
0 -0.063404  0.339041  0.124552   -0.002445  
1  1.831241 -0.659091  0.047114   -0.490365  
2  0.114836  0.535974  0.743338    0.204952  
3 -0.417514  0.911652 -0.296168    1.073948  
4  0.729495  0.245109  1.526606    2.614378  

[5 rows x 35 columns]

In [4]:
Y_train.head()

ID    TARGET
0  1054  0.028313
1  2049 -0.112516
2  1924 -0.180840
3   297 -0.260356
4  1101 -0.071733

## Feature engineering

#### General function

In [5]:
def slope(y):
    return np.polyfit(range(len(y)), y, 1)[0] if len(y) > 0 else np.nan

def calculate_ema(data, window):
    return data.ewm(span=window, adjust=False).mean()

def calculate_rsi(data, window=14):
    delta = data.diff(1)
    gain = (delta.where(delta > 0, 0)).rolling(window=window).mean()
    loss = (-delta.where(delta < 0, 0)).rolling(window=window).mean()

    rs = gain / loss
    rsi = 100 - (100 / (1 + rs))
    return rsi

def calculate_bollinger_bands(data, window=20):
    sma = data.rolling(window=window).mean()
    std = data.rolling(window=window).std()
    
    bollinger_upper = sma + (std * 2)
    bollinger_lower = sma - (std * 2)
    
    return bollinger_upper, bollinger_lower

In [6]:
def feature_engineering(X, Y):
    df = X.copy()
    df.fillna(0, inplace=True)
    
    # Temporal window
    windows = [7, 30]

    # Column to calculate statistic
    variables = ['CONSUMPTION', 'GAS', 'COAL', 'HYDRO', 'NUCLEAR', 'SOLAR', 'WINDPOW', 'TEMP', 'RAIN', 'WIND']
    
    def slope(y):
        return np.polyfit(range(len(y)), y, 1)[0] if len(y) > 0 else np.nan

    for var in variables:
        for window in windows:
            for country in ['DE_', 'FR_']:
                # Mean, Standard deviation, Median, Minimum, Maximum, Slope
                df[f'{country}{var}_MEAN_{window}D'] = df[f'{country}{var}'].rolling(window=window).mean()
                df[f'{country}{var}_STD_{window}D'] = df[f'{country}{var}'].rolling(window=window).std()
                df[f'{country}{var}_MEDIAN_{window}D'] = df[f'{country}{var}'].rolling(window=window).median()
                df[f'{country}{var}_MIN_{window}D'] = df[f'{country}{var}'].rolling(window=window).min()
                df[f'{country}{var}_MAX_{window}D'] = df[f'{country}{var}'].rolling(window=window).max()
                df[f'{country}{var}_SLOPE_{window}D'] = df[f'{country}{var}'].rolling(window=window).apply(slope, raw=True)

                # Additional features based on the original request
                if var in ['CONSUMPTION', 'GAS', 'COAL', 'HYDRO', 'NUCLEAR', 'SOLAR', 'WINDPOW']:  # For RSI and Bollinger Bands
                    df[f'{country}{var}_RSI'] = calculate_rsi(df[f'{country}{var}'])
                    df[f'{country}{var}_BB_UPPER'], df[f'{country}{var}_BB_LOWER'] = calculate_bollinger_bands(df[f'{country}{var}'])
    
    # Seasonality Features
    days_in_year = 365.25
    df['SIN_YEAR'] = np.sin(2 * np.pi * df['DAY_ID'] / days_in_year)
    df['COS_YEAR'] = np.cos(2 * np.pi * df['DAY_ID'] / days_in_year)
    
    days_in_week = 7
    df['SIN_WEEK'] = np.sin(2 * np.pi * df['DAY_ID'] / days_in_week)
    df['COS_WEEK'] = np.cos(2 * np.pi * df['DAY_ID'] / days_in_week)

    df['SEASON'] = pd.cut(df['DAY_ID'] % 365, 
                          bins=[0, 79, 172, 264, 365], 
                          labels=[0, 1, 2, 3],
                          right=False).astype(int)
    
    for energy_source in ['GAS', 'COAL', 'HYDRO', 'NUCLEAR', 'SOLAR', 'WINDPOW', 'LIGNITE']:
        df[f'DE_{energy_source}_RATIO'] = df[f'DE_{energy_source}'] / (df['DE_GAS'] + df['DE_COAL'] + df['DE_HYDRO'] + df['DE_NUCLEAR'] + df['DE_SOLAR'] + df['DE_WINDPOW'] + df['DE_LIGNITE'])

    df['DE_IMPORT_RATIO'] = df['DE_NET_IMPORT'] / df['DE_CONSUMPTION']
    df['DE_EXPORT_RATIO'] = df['DE_NET_EXPORT'] / (df['DE_GAS'] + df['DE_COAL'] + df['DE_HYDRO'] + df['DE_NUCLEAR'] + df['DE_SOLAR'] + df['DE_WINDPOW'] + df['DE_LIGNITE'])

    df['DE_FR_NET_EXCHANGE'] = df['DE_FR_EXCHANGE'] - df['FR_DE_EXCHANGE']

    df['DE_WIND_SOLAR'] = df['DE_WINDPOW'] + df['DE_SOLAR']
    df['DE_TEMP_EFFECT'] = df['DE_TEMP'] * df['DE_CONSUMPTION']
    df['DE_WIND_EFFECT'] = df['DE_WIND'] * df['DE_WINDPOW']
    df['DE_SOLAR_EFFECT'] = (df['DE_SOLAR'] / df['DE_TEMP']).replace([np.inf, -np.inf], np.nan).fillna(0)

    for commodity in ['GAS_RET', 'COAL_RET', 'CARBON_RET']:
        df[f'{commodity}_VOLATILITY_7D'] = df[commodity].rolling(window=7).std()
        df[f'{commodity}_VOLATILITY_30D'] = df[commodity].rolling(window=30).std()

    for commodity in ['GAS_RET', 'COAL_RET', 'CARBON_RET']:
        df[f'{commodity}_EMA_30D'] = df[commodity].ewm(span=30, adjust=False).mean()

    df['DE_RESIDUAL_LOAD_RATIO'] = df['DE_RESIDUAL_LOAD'] / df['DE_CONSUMPTION']
    df['DE_Imbalance'] = (df['DE_GAS'] + df['DE_COAL'] + df['DE_HYDRO'] + df['DE_NUCLEAR'] + df['DE_SOLAR'] + df['DE_WINDPOW'] + df['DE_LIGNITE']) - df['DE_CONSUMPTION'] - df['DE_NET_EXPORT']
    
    for energy_source in ['GAS', 'COAL', 'HYDRO', 'NUCLEAR', 'SOLAR', 'WINDPOW']:
        df[f'FR_{energy_source}_RATIO'] = df[f'FR_{energy_source}'] / (df['FR_GAS'] + df['FR_COAL'] + df['FR_HYDRO'] + df['FR_NUCLEAR'] + df['FR_SOLAR'] + df['FR_WINDPOW'])

    df['FR_IMPORT_RATIO'] = df['FR_NET_IMPORT'] / df['FR_CONSUMPTION']
    df['FR_EXPORT_RATIO'] = df['FR_NET_EXPORT'] / (df['FR_GAS'] + df['FR_COAL'] + df['FR_HYDRO'] + df['FR_NUCLEAR'] + df['FR_SOLAR'] + df['FR_WINDPOW'])

    df['FR_WIND_SOLAR'] = df['FR_WINDPOW'] + df['FR_SOLAR']
    df['FR_TEMP_EFFECT'] = df['FR_TEMP'] * df['FR_CONSUMPTION']
    df['FR_WIND_EFFECT'] = df['FR_WIND'] * df['FR_WINDPOW']
    df['FR_SOLAR_EFFECT'] = (df['FR_SOLAR'] / df['FR_TEMP']).replace([np.inf, -np.inf], np.nan).fillna(0)

    df['FR_WIND_SOLAR'] = df['FR_WINDPOW'] + df['FR_SOLAR']
    df['FR_TEMP_EFFECT'] = df['FR_TEMP'] * df['FR_CONSUMPTION']
    df['FR_WIND_EFFECT'] = df['FR_WIND'] * df['FR_WINDPOW']
    df['FR_SOLAR_EFFECT'] = (df['FR_SOLAR'] / df['FR_TEMP']).replace([np.inf, -np.inf], np.nan).fillna(0)

    df['FR_RESIDUAL_LOAD_RATIO'] = df['FR_RESIDUAL_LOAD'] / df['FR_CONSUMPTION']
    df['FR_Imbalance'] = (df['FR_GAS'] + df['FR_COAL'] + df['FR_HYDRO'] + df['FR_NUCLEAR'] + df['FR_SOLAR'] + df['FR_WINDPOW']) - df['FR_CONSUMPTION'] - df['FR_NET_EXPORT']
    
    # Ensuring all missing data filled if any new were created
    df.fillna(method='bfill', inplace=True)

    return df

In [7]:
X_featurized = feature_engineering(X_train.drop(['COUNTRY'], axis=1), Y_train['TARGET'])
print(f"Final number of columns: {len(X_featurized.columns)}")

Final number of columns: 360


## Modèles et score d'entrainement

Le benchmark pour ce challenge consiste en une simple régression linéaire, après un léger nettoyage des données : Les valeurs manquantes (NaN) ont été remplacées par des zéros et la colonne `COUNTRY` a été supprimée - en d'autres termes, nous avons utilisé un modèle identique pour la France et l'Allemagne.

#### Use of a "naive" and simple LGBM model

In [8]:
X_train, X_test, y_train, y_test = train_test_split(X_featurized, Y_train['TARGET'], test_size=0.2, random_state=42)

params = {
    'objective': 'regression',
    'metric': 'rmse',
    'learning_rate': 0.1,
    'num_leaves': 31,
    'verbose': -1
}

train_data = lgb.Dataset(X_train, label=y_train)
gbm = lgb.train(params, train_data, num_boost_round=100)

predictions_train = gbm.predict(X_train)
spearman_corr_train = spearmanr(predictions_train, y_train).correlation
print("Corrélation (Spearman) pour les données de test : {:.1f}%".format(100 * spearman_corr_train))

predictions_test = gbm.predict(X_test)
spearman_corr_test = spearmanr(predictions_test, y_test).correlation
print("Corrélation (Spearman) pour les données de test : {:.1f}%".format(100 * spearman_corr_test))

Corrélation (Spearman) pour les données de test : 98.1%
Corrélation (Spearman) pour les données de test : 9.9%


In [9]:
X_test = pd.read_csv('../data/X_test.csv')
y_test = pd.read_csv('../data/y_test.csv')

X_featurized_test = feature_engineering(X_test.drop(['COUNTRY'], axis=1), y_test["TARGET"])
predictions_test = gbm.predict(X_featurized_test)
spearman_corr_test = spearmanr(predictions_test, y_test["TARGET"]).correlation

print("Corrélation (Spearman) pour les données de test : {:.1f}%".format(100 * spearman_corr_test))

Corrélation (Spearman) pour les données de test : -1.5%


#### Use of GridSearch to find optimal hyperparameters

In [10]:
# Définition de l'espace des hyperparamètres
param_grid = {
    'learning_rate': [0.05, 0.1, 0.2],
    'num_leaves': [20, 31, 40, 50],
    'max_depth': [-1, 10, 20],
    'lambda_l1': [0, 0.1, 0.5],
    'lambda_l2': [0, 0.1, 0.5]
}

# Configuration du modèle pour la recherche d'hyperparamètres
model = LGBMRegressor(objective='regression', metric='rmse', random_state=42)

# Création du scorer basé sur RMSE
rmse_scorer = make_scorer(mean_squared_error, greater_is_better=False, squared=False)

# Configuration de GridSearchCV
grid_search = GridSearchCV(estimator=model, param_grid=param_grid, cv=5, scoring=rmse_scorer, verbose=1)

# Recherche des meilleurs hyperparamètres sur l'ensemble d'entraînement
grid_search.fit(X_train, y_train)

Fitting 5 folds for each of 324 candidates, totalling 1620 fits
[LightGBM] [Warning] lambda_l1 is set=0, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0
[LightGBM] [Warning] lambda_l2 is set=0, reg_lambda=0.0 will be ignored. Current value: lambda_l2=0
[LightGBM] [Warning] lambda_l1 is set=0, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0
[LightGBM] [Warning] lambda_l2 is set=0, reg_lambda=0.0 will be ignored. Current value: lambda_l2=0
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.006604 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 80204
[LightGBM] [Info] Number of data points in the train set: 956, number of used features: 360
[LightGBM] [Info] Start training from score 0.073742
[LightGBM] [Warning] lambda_l1 is set=0, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0
[LightGBM] [Warning] lambda_l2 is set=0, reg_lambda=0.0 will be ignored. Current value: lambda_l2

GridSearchCV(cv=5,
             estimator=LGBMRegressor(metric='rmse', objective='regression',
                                     random_state=42),
             param_grid={'lambda_l1': [0, 0.1, 0.5], 'lambda_l2': [0, 0.1, 0.5],
                         'learning_rate': [0.05, 0.1, 0.2],
                         'max_depth': [-1, 10, 20],
                         'num_leaves': [20, 31, 40, 50]},
             scoring=make_scorer(mean_squared_error, greater_is_better=False, response_method='predict', squared=False),
             verbose=1)

In [16]:
# Utilisation du meilleur modèle trouvé par GridSearchCV
best_model = grid_search.best_estimator_
dump(best_model, '../models/best_lgbm_model.joblib')

X_train, X_test, y_train, y_test = train_test_split(X_featurized, Y_train['TARGET'], test_size=0.2, random_state=42)

# Prédictions et évaluation sur l'ensemble d'entraînement
predictions_train = best_model.predict(X_train)
spearman_corr_train = spearmanr(predictions_train, y_train).correlation
print("Corrélation (Spearman) pour les données d'entraînement : {:.1f}%".format(100 * spearman_corr_train))

# Prédictions et évaluation sur l'ensemble de test
predictions_test = best_model.predict(X_test)
spearman_corr_test = spearmanr(predictions_test, y_test).correlation
print("Corrélation (Spearman) pour les données de test : {:.1f}%".format(100 * spearman_corr_test))

[LightGBM] [Warning] lambda_l1 is set=0.5, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.5
[LightGBM] [Warning] lambda_l2 is set=0, reg_lambda=0.0 will be ignored. Current value: lambda_l2=0
Corrélation (Spearman) pour les données d'entraînement : 87.1%
[LightGBM] [Warning] lambda_l1 is set=0.5, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.5
[LightGBM] [Warning] lambda_l2 is set=0, reg_lambda=0.0 will be ignored. Current value: lambda_l2=0
Corrélation (Spearman) pour les données de test : 8.6%


In [17]:
X_test = pd.read_csv('../data/X_test.csv')
y_test = pd.read_csv('../data/y_test.csv')

X_featurized_test = feature_engineering(X_test.drop(['COUNTRY'], axis=1), y_test["TARGET"])
predictions_test = best_model.predict(X_featurized_test)
spearman_corr_test = spearmanr(predictions_test, y_test["TARGET"]).correlation

print("Corrélation (Spearman) pour les données de test : {:.1f}%".format(100 * spearman_corr_test))

[LightGBM] [Warning] lambda_l1 is set=0.5, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.5
[LightGBM] [Warning] lambda_l2 is set=0, reg_lambda=0.0 will be ignored. Current value: lambda_l2=0
Corrélation (Spearman) pour les données de test : -1.2%


La corrélation de Spearman obtenue avec notre modèle sur les données d'entrainement est d'environ 27.9%.

NB : Les variations du prix de l'électricité peuvent être très volatiles et c'est pour cette raison que nous avons préféré la corrélation de Spearman à la corrélation usuelle (Pearson), pour avoir une fonction de score plus robuste.

## Générer le benchmark

Pour générer le benchmark on procède comme on l'a fait avec les données d'entrainement mais cette fois sur les données test, et on renvoie la sortie au format csv adapté aux contraintes des sorties du challenge.  


In [14]:
X_test = pd.read_csv('../data/X_test.csv')
y_test = pd.read_csv('../data/y_test.csv')

X_featurized_test = feature_engineering(X_test.drop(['COUNTRY'], axis=1), y_test["TARGET"])
predictions_test = best_model.predict(X_featurized_test)

Y_test_submission = X_test[['ID']].copy()
Y_test_submission['TARGET'] = predictions_test
Y_test_submission.to_csv('submission_lgbm.csv', index=False)

[LightGBM] [Warning] lambda_l1 is set=0.5, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.5
[LightGBM] [Warning] lambda_l2 is set=0, reg_lambda=0.0 will be ignored. Current value: lambda_l2=0
